In [33]:
import numpy as np
import scipy as sp
import matplotlib.pyplot as plt
import os,sys
#sys.path.append(os.path.expanduser('~')+'/audio_class/python')
sys.path.append('../../audio_class/python')
from IPython.display import Audio
import utils
import ridgeDTW
import multiprocessing
from joblib import Parallel,delayed

os.system("taskset -p 0xff %d" % os.getpid())

%matplotlib inline
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [9]:
DATAROOT = './BBSPjun5_13/'

In [30]:
for file in os.listdir(DATAROOT):
    print(file)
    fs,data = utils.readSegment(DATAROOT+file)
    break

day2-1370485107.wav
N = 2646000
nbytes = 2
len(buf) = 42336000


In [31]:
print('fs = %s' % fs)
(nCh,nDat) = np.shape(data)
print('nCh = %s, nDat = %s' % (nCh,nDat))
Audio(data[0,:],rate=fs)

fs = 44100


In [ ]:
def ridgePar(k,data,fs,btTime):
    S,F,T,tBlk,tInc = utils.spectrographic(data[k,:],fs,0.032,0.016,1024)
    X = ridgeDTW.ridgeTracker(S,np.median(S.flatten()),btTime,tInc,isMaxPool=True)
    return X

btTime = 0.008
Xs = Parallel(n_jobs=multiprocessing.cpu_count())(delayed(ridgePar)(k,data,fs,btTime) for k in range(nCh))

In [ ]:
plt.figure(figsize=(12,12))
for k in range(nCh):
    plt.subplot(nCh,1,1+k)
    plt.pcolormesh(T,F,np.sqrt(Xs[k]))